In [0]:
# Read datasets
tickets_df = spark.read.csv("s3a://gully-bots-retail-chatbot-1/synthetic_support_tickets_1M.csv", header=True, inferSchema=True)
policy_df = spark.read.csv("s3a://gully-bots-retail-chatbot-1/return_refund_policy.csv", header=True, inferSchema=True)


In [0]:
tickets_df.count()

Out[5]: 1000000

In [0]:
policy_df.count()

Out[6]: 15

In [0]:
from pyspark.sql.functions import col

tickets_df.select([col(c).isNull().alias(c) for c in tickets_df.columns]).summary("count").show()


+-------+
|summary|
+-------+
|  count|
+-------+



In [0]:
# Check Customer Age and Satisfaction Ratings range
tickets_df.filter((col("Customer Age") < 18) | (col("Customer Age") > 65)).show()
tickets_df.filter((col("Customer Satisfaction Rating") < 1) | (col("Customer Satisfaction Rating") > 5)).show()


+---------+-------------+--------------+------------+---------------+-----------------+----------------+-----------+--------------+------------------+-------------+----------+---------------+--------------+-------------------+------------------+----------------------------+
|Ticket ID|Customer Name|Customer Email|Customer Age|Customer Gender|Product Purchased|Date of Purchase|Ticket Type|Ticket Subject|Ticket Description|Ticket Status|Resolution|Ticket Priority|Ticket Channel|First Response Time|Time to Resolution|Customer Satisfaction Rating|
+---------+-------------+--------------+------------+---------------+-----------------+----------------+-----------+--------------+------------------+-------------+----------+---------------+--------------+-------------------+------------------+----------------------------+
+---------+-------------+--------------+------------+---------------+-----------------+----------------+-----------+--------------+------------------+-------------+----------+

In [0]:
# Ensure date format and field type consistency
tickets_df.select("Date of Purchase").printSchema()


root
 |-- Date of Purchase: date (nullable = true)



In [0]:
# Check Gender conformity
tickets_df.select("Customer Gender").distinct().show()


+---------------+
|Customer Gender|
+---------------+
|         Female|
|     Non-binary|
|           Male|
+---------------+



In [0]:
# Check joinability
tickets_df.join(policy_df, tickets_df["Product Purchased"] == policy_df["product_name"], "left_anti").show()


+---------+-------------+--------------+------------+---------------+-----------------+----------------+-----------+--------------+------------------+-------------+----------+---------------+--------------+-------------------+------------------+----------------------------+
|Ticket ID|Customer Name|Customer Email|Customer Age|Customer Gender|Product Purchased|Date of Purchase|Ticket Type|Ticket Subject|Ticket Description|Ticket Status|Resolution|Ticket Priority|Ticket Channel|First Response Time|Time to Resolution|Customer Satisfaction Rating|
+---------+-------------+--------------+------------+---------------+-----------------+----------------+-----------+--------------+------------------+-------------+----------+---------------+--------------+-------------------+------------------+----------------------------+
+---------+-------------+--------------+------------+---------------+-----------------+----------------+-----------+--------------+------------------+-------------+----------+

In [0]:
from pyspark.sql.functions import current_date, datediff

tickets_df.withColumn("DaysSincePurchase", datediff(current_date(), col("Date of Purchase"))) \
          .filter("DaysSincePurchase > 365 OR DaysSincePurchase < 0").show()


+-----------+------------------+--------------------+------------+---------------+--------------------+----------------+-----------+--------------------+--------------------+-------------+--------------------+---------------+--------------+-------------------+------------------+----------------------------+-----------------+
|  Ticket ID|     Customer Name|      Customer Email|Customer Age|Customer Gender|   Product Purchased|Date of Purchase|Ticket Type|      Ticket Subject|  Ticket Description|Ticket Status|          Resolution|Ticket Priority|Ticket Channel|First Response Time|Time to Resolution|Customer Satisfaction Rating|DaysSincePurchase|
+-----------+------------------+--------------------+------------+---------------+--------------------+----------------+-----------+--------------------+--------------------+-------------+--------------------+---------------+--------------+-------------------+------------------+----------------------------+-----------------+
|TCKT1000220|     A

In [0]:
merged_df = tickets_df.join(policy_df, tickets_df["Product Purchased"] == policy_df["product_name"], "left")

# Optional cleanup
final_df = merged_df.drop("product_name")

# Save to Parquet for LangChain or write to S3
final_df


Out[14]: DataFrame[Ticket ID: string, Customer Name: string, Customer Email: string, Customer Age: int, Customer Gender: string, Product Purchased: string, Date of Purchase: date, Ticket Type: string, Ticket Subject: string, Ticket Description: string, Ticket Status: string, Resolution: string, Ticket Priority: string, Ticket Channel: string, First Response Time: string, Time to Resolution: string, Customer Satisfaction Rating: int, category: string, return_window_days: int, refund_allowed: string, replacement_allowed: string, restocking_fee: string, return_policy_description: string]

In [0]:
final_df.count()

Out[16]: 1000000

In [0]:
final_df.display()


Ticket ID Customer Name Customer Email Customer Age Customer Gender Product Purchased Date of Purchase Ticket Type Ticket Subject Ticket Description Ticket Status Resolution Ticket Priority Ticket Channel First Response Time Time to Resolution Customer Satisfaction Rating category return_window_days refund_allowed replacement_allowed restocking_fee return_policy_description TCKT1000000 Sarah Waller sarah.waller@example.com 38 Male Amazon Brand - Solimo Designer 3D Printed Case for iPhone 13 2024-11-28 Query Query regarding Amazon Brand - Solimo Designer 3D Printed Case for iPhone 13 Is the Amazon Brand - Solimo Designer 3D Printed Case for iPhone 13 compatible with my device model? Resolved Customer query answered with additional product care tips. Low Email 535 minutes 147 hours 5 Mobile Accessories 15 Yes Yes No Must be returned in original condition with packaging. TCKT1000001 Karen Johnson karen.johnson@example.com 47 Male Anker USB-C Fast Charger 20W 2024-10-21 Feedback Feedback regarding Anker USB-C Fast Charger 20W The Anker USB-C Fast Charger 20W design is nice, but I expected more durability. Open Customer query answered with additional product care tips. Low Email 1053 minutes 24 hours 4 Mobile Accessories 15 Yes Yes No Must be returned in original condition with packaging. TCKT1000002 Brenda Brown brenda.brown@example.com 27 Male JBL Flip 5 Bluetooth Speaker 2024-06-12 Complaint Complaint regarding JBL Flip 5 Bluetooth Speaker The JBL Flip 5 Bluetooth Speaker stopped working after just one week of use. Escalated Replacement issued and return initiated. Medium Web 1617 minutes 122 hours 2 Electronics 10 Yes Yes (limited) No Refund only on manufacturing defects, no cosmetic damage. TCKT1000003 Nathan Stewart nathan.stewart@example.com 64 Female Urban Outfitters Tufted Floor Cushion 2024-06-26 Issue Issue regarding Urban Outfitters Tufted Floor Cushion The Urban Outfitters Tufted Floor Cushion sheds fibers excessively even after vacuuming. Resolved Customer query answered with additional product care tips. Medium Email 128 minutes 59 hours 5 Home Decor 30 Yes Yes 10% Return accepted only if unused and undamaged. TCKT1000004 Dominique Howell dominique.howell@example.com 60 Male Mi Power Bank 20000mAh 2025-02-01 Feedback Feedback regarding Mi Power Bank 20000mAh Loved the sound and battery life of the Mi Power Bank 20000mAh. Closed Customer query answered with additional product care tips. Medium Web 2786 minutes 86 hours 1 Electronics 10 Yes Yes (limited) No Refund only on manufacturing defects, no cosmetic damage. TCKT1000005 Kelly Brown kelly.brown@example.com 46 Female Amazon Brand - Solimo Designer 3D Printed Case for iPhone 13 2024-12-08 Query Query regarding Amazon Brand - Solimo Designer 3D Printed Case for iPhone 13 Is the Amazon Brand - Solimo Designer 3D Printed Case for iPhone 13 compatible with my device model? Closed Customer query answered with additional product care tips. Low Web 642 minutes 130 hours 1 Mobile Accessories 15 Yes Yes No Must be returned in original condition with packaging. TCKT1000006 Joseph Zhang joseph.zhang@example.com 25 Male Fire TV Stick 4K 2024-12-15 Issue Issue regarding Fire TV Stick 4K My Fire TV Stick 4K gets unusually hot while in use. Is this expected? Open Customer query answered with additional product care tips. Medium Phone 645 minutes 92 hours 3 Electronics 10 Yes Yes (limited) No Refund only on manufacturing defects, no cosmetic damage. TCKT1000007 Tammy Taylor tammy.taylor@example.com 45 Female Amazon Brand - Solimo Designer 3D Printed Case for iPhone 13 2025-03-12 Complaint Complaint regarding Amazon Brand - Solimo Designer 3D Printed Case for iPhone 13 The Amazon Brand - Solimo Designer 3D Printed Case for iPhone 13 doesn't fit properly and the cutouts are off. Escalated Replacement issued and return initiated. High Email 2021 minutes 51 hours 5 Mobile Accessories 15 Yes Yes No Must be returned in original condition with packaging. TCKT1000008 Collin Potts collin.po